# Upward body Movement tracking system using mediapipe #

In [1]:
#Installing needed liberies 
!pip install mediapipe opencv-python html


  Using cached html-1.16.tar.gz (7.6 kB)
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'error'


  error: subprocess-exited-with-error
  
  python setup.py egg_info did not run successfully.
  exit code: 1
  
  [7 lines of output]
  Traceback (most recent call last):
    File "<string>", line 2, in <module>
    File "<pip-setuptools-caller>", line 35, in <module>
    File "C:\Users\abeed\AppData\Local\Temp\pip-install-nlmddqdx\html_5f2029f8f4394d1391cdf128791204cc\setup.py", line 12, in <module>
      long_description = __doc__.decode('utf8'),
                         ^^^^^^^^^^^^^^
  AttributeError: 'str' object has no attribute 'decode'. Did you mean: 'encode'?
  [end of output]
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
error: metadata-generation-failed

Encountered error while generating package metadata.

See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.


### Importing Liberies ###

In [2]:
#importing Basic Needed liberies
import cv2
import mediapipe as mp
import numpy as np
mp_drwawing = mp.solutions.drawing_utils
mp_pose=mp.solutions.pose

### Test Camera ###

In [3]:
#testing camera and capturing. Taking live camera feed
cap= cv2.VideoCapture(0) #Connecting the camera 
while cap.isOpened():
    ret,frame= cap.read()
    cv2.imshow("live camera feed", frame)


    if cv2.waitKey(10) & 0xFF == ord("x"):
        break
cap.release()
cv2.destroyAllWindows()

### Insights from the feed

In [7]:


cap= cv2.VideoCapture(0) #Connecting the camera 
with mp_pose.Pose(min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
    while cap.isOpened():
        ret,frame= cap.read()
        

        #Converting the video to opencv format-Recoloring
        #BGR to RBG
        image=cv2.cvtColor(frame,cv2.COLOR_BGR2RGB)
        image.flags.writeable= False
        
        #Detection
        results= pose.process(image)

        #recolor to BGR
        image.flags.writeable= True
        image=cv2.cvtColor(frame,cv2.COLOR_RGB2BGR)

        #extracting the landmarks frm the videos
        try:
            landmarks= results.pose_landmarks.landmark
            print(landmarks)
        except:
            pass

        #rendering the image
        mp_drwawing.draw_landmarks(image,results.pose_landmarks, mp_pose.POSE_CONNECTIONS)

        #extracting the landmarks frm the videos
        

        print(results)

        prev_nose_y = None
        prev_ankle_y = None
        

        if results.pose_landmarks:
            lm= results.pose_landmarks.landmark
            nose_y = lm[mp_pose.PoseLandmark.NOSE.value].y
            left_ankle_y = lm[mp_pose.PoseLandmark.LEFT_ANKLE.value].y
            right_ankle_y = lm[mp_pose.PoseLandmark.RIGHT_ANKLE.value].y
            avg_leg = (left_ankle_y + right_ankle_y)/2.0

        # approximate height of the person standing
            height= nose_y - avg_leg
            if prev_nose_y is not None and prev_ankle_y is not None:
                change_N = (prev_nose_y) - (nose_y)
                change_A = (prev_ankle_y) - (avg_leg)

                #Crose-check the difference
                change= abs(change_N - change_A)
                #mean motion
                jump=(nose_y + avg_leg)/2.0


                print(change_N)
                print(change_A)
                print(change)
                print(jump)


            prev_nose_y = nose_y
            prev_ankle_y = avg_leg



        cv2.imshow("live camera feed", image)

        if cv2.waitKey(10) & 0xFF == ord("x"):
            break
    cap.release()
    cv2.destroyAllWindows()

[x: 0.612017
y: 0.787602663
z: -1.59912395
visibility: 0.987990797
, x: 0.644116342
y: 0.704526186
z: -1.58714116
visibility: 0.974797249
, x: 0.665941477
y: 0.699928284
z: -1.58720839
visibility: 0.980720341
, x: 0.686092257
y: 0.694822907
z: -1.58811116
visibility: 0.974640071
, x: 0.578303874
y: 0.705606341
z: -1.58629239
visibility: 0.978392243
, x: 0.557423592
y: 0.702010512
z: -1.58551562
visibility: 0.983052969
, x: 0.537997961
y: 0.698550105
z: -1.5860709
visibility: 0.980184138
, x: 0.72341913
y: 0.686018586
z: -1.12164
visibility: 0.984902442
, x: 0.518354177
y: 0.70351994
z: -1.09007335
visibility: 0.991644442
, x: 0.652116477
y: 0.852295876
z: -1.38860869
visibility: 0.992551446
, x: 0.577085674
y: 0.854558349
z: -1.37965882
visibility: 0.994061172
, x: 0.895162
y: 0.91977
z: -0.587131917
visibility: 0.995806456
, x: 0.370373785
y: 0.908611417
z: -0.652949274
visibility: 0.998012424
, x: 1.00477552
y: 1.33786237
z: -0.32489
visibility: 0.209536344
, x: 0.19668901
y: 1.12909

### Check the output variables 

In [ ]:
print(results)

### Testing the landmarks

In [13]:
#Getting a landmark coordinates from the video. Example of a nose is showed below similiarly all landmarks coordinate can be obtained using diffenent syntax
landmarks[mp_pose.PoseLandmark.NOSE.value]

x: 0.590165079
y: 0.93455708
z: -0.781745553
visibility: 0.994869

In [20]:
landmarks[mp_pose.PoseLandmark.LEFT_SHOULDER.value]

x: 0.752882123
y: 1.11823845
z: -0.184591591
visibility: 0.787649274

### Caluation of the Jump


In [25]:
prev_nose_y= None
prev_ankle_y = None

if landmarks:
    lm= np.array(results.pose_landmarks.landmark)
    nose_y=np.array(lm[mp_pose.PoseLandmark.NOSE.value].y)
    left_ankle_y=np.array(lm[mp_pose.PoseLandmark.LEFT_ANKLE.value].y)
    right_ankle_y=np.array(lm[mp_pose.PoseLandmark.RIGHT_ANKLE.value].y)
    avg_leg=(left_ankle_y + right_ankle_y)/2.0

# approximate height of the person standing
    height= nose_y - avg_leg
    if prev_nose_y is not None and prev_ankle_y is not None:
        change_N= (prev_nose_y) - (nose_y)
        change_A= (prev_ankle_y) - (avg_leg)

        #Crose-check the difference
        change= abs(change_N - change_A)
        #mean motion
        jump=(nose_y + avg_leg)/2.0


    prev_nose_y=nose_y
    prev_ankle_y = avg_leg

        

In [ ]:
< img src="https://i.imgur.com/3j8BPdc.png" style="height: 300px">-->